# MODELIŲ MOKYMAS IR GERIAUSIŲ PARAMETRŲ PAIEŠKA

In [ ]:
import pandas as pd
reviews = pd.read_csv('trustpilot_coinbase_reviews-strip.csv', sep='|')
reviews.tail()

Date                                              Title  Rating
6475  2017-05-22              Very bad.I can't register any of my …     1.0
6476  2017-05-19  Functional platform but seriously lacking in c...     3.0
6477  2017-05-18                                   No reservations.     5.0
6478  2017-05-18              I HOPE YOU SEE THIS BEFORE You send …     1.0
6479  2017-05-16                Coinbase - the rock star crypto app     4.0

In [ ]:
import pandas as pd
import numpy as np
from sklearn.linear_model import LinearRegression
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score


def mean_absolute_percentage_error(y_true, y_pred):
    y_true, y_pred = np.array(y_true), np.array(y_pred)
    return np.mean(np.abs((y_true - y_pred) / y_true)) * 100

def eval_regression(X_train, X_test, y_train, y_test, model, description):
    model.fit(X_train, y_train)
    y_pred = model.predict(X_test)
    
    mse = mean_squared_error(y_test, y_pred)
    mae = mean_absolute_error(y_test, y_pred)
    r2 = r2_score(y_test, y_pred)
    mape = mean_absolute_percentage_error(y_test, y_pred)
    
    print(description)
    print(f"Mean Squared (MSE): {mse:.2f}")
    print(f"Mean Absolute Error (MAE): {mae:.2f}")
    print(f"R^2: {r2:.2f}")
    print(f"Mean Absolute % (MAPE): {mape:.2f}%")
    print('='*50 + '\n')
btc_all = pd.read_csv('combined_btc_data.csv')

btc_all['Date'] = pd.to_datetime(btc_all['Date'])
btc_all['Day'] = btc_all['Date'].dt.day
btc_all['Month'] = btc_all['Date'].dt.month
btc_all['Year'] = btc_all['Date'].dt.year

# Create lag
btc_all['Lag_Close_1'] = btc_all['Close'].shift(1)
btc_all['Lag_Close_2'] = btc_all['Close'].shift(2)
btc_all['Lag_Volume_1'] = btc_all['Volume'].shift(1)
btc_all['Lag_Volume_2'] = btc_all['Volume'].shift(2)

btc_all.dropna(inplace=True)

X = btc_all[['Lag_Close_1', 'Lag_Close_2', 'Lag_Volume_1', 'Lag_Volume_2', 'Day', 'Month', 'Year']]
y = btc_all['Close']

btc_all.sort_values('Date', inplace=True)

split_point = int(len(btc_all) * 0.85) # only newest data for test to prevent leakage

X_train = X.iloc[:split_point]
X_test = X.iloc[split_point:]
y_train = y.iloc[:split_point]
y_test = y.iloc[split_point:]

# Normalize
scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)

model = LinearRegression()

eval_regression(X_train, X_test, y_train, y_test, model, "Linear Regression Model:")

Linear Regression Model:
Mean Squared (MSE): 1309806.40
Mean Absolute Error (MAE): 700.22
R^2: 0.99
Mean Absolute % (MAPE): 1.72%



### PRIDEDAME TRUSTPILOT REITINGUS

In [ ]:
import pandas as pd
from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import LinearRegression

btc_all = pd.read_csv('combined_btc_data.csv')
reviews = pd.read_csv('trustpilot_coinbase_reviews-strip.csv', sep='|')

reviews = reviews[reviews['Date'].apply(is_date)]
reviews['Date'] = pd.to_datetime(reviews['Date'])

reviews['YearMonth'] = reviews['Date'].dt.to_period('M')

monthly_mean_rating = reviews.groupby('YearMonth')['Rating'].mean().reset_index()
monthly_mean_rating['Date'] = monthly_mean_rating['YearMonth'].dt.to_timestamp()

btc_all['Date'] = pd.to_datetime(btc_all['Date'])

# date for monthly_mean_rating
btc_all['YearMonth'] = btc_all['Date'].dt.to_period('M')

btc_all = pd.merge(btc_all, monthly_mean_rating, on='YearMonth', how='left')
btc_all['Date'] =  btc_all['Date_x']
btc_all = btc_all.drop(columns=['Date_x', 'Date_y'])

btc_all['Rating'].fillna(method='ffill', inplace=True)

btc_all['Lag_Close_1'] = btc_all['Close'].shift(1)
btc_all['Lag_Close_2'] = btc_all['Close'].shift(2)
btc_all['Lag_Volume_1'] = btc_all['Volume'].shift(1)
btc_all['Lag_Volume_2'] = btc_all['Volume'].shift(2)

btc_all.dropna(inplace=True)

btc_all['Day'] = btc_all['Date'].dt.day
btc_all['Month'] = btc_all['Date'].dt.month
btc_all['Year'] = btc_all['Date'].dt.year

X = btc_all[['Lag_Close_1', 'Lag_Close_2', 'Lag_Volume_1', 'Lag_Volume_2', 'Day', 'Month', 'Year', 'Rating']]
y = btc_all['Close']

btc_all.sort_values('Date', inplace=True)

split_point = int(len(btc_all) * 0.85) # 15% of most recent data for testing
X_train = X.iloc[:split_point]
X_test = X.iloc[split_point:]
y_train = y.iloc[:split_point]
y_test = y.iloc[split_point:]

scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)

model = LinearRegression()
model.fit(X_train, y_train)

eval_regression(X_train, X_test, y_train, y_test, model, "Linear Regression Model (with added Coinmarketcap rating feature):")

Linear Regression Model (with added Coinmarketcap rating feature):
Mean Squared (MSE): 1601648.70
Mean Absolute Error (MAE): 779.05
R^2: 0.99
Mean Absolute % (MAPE): 1.67%



# GridSearch paieška / POLYNOMIAL 

In [ ]:
import pandas as pd
from sklearn.preprocessing import StandardScaler, PolynomialFeatures
from sklearn.linear_model import LinearRegression
from sklearn.model_selection import GridSearchCV
from sklearn.pipeline import Pipeline

btc_all = pd.read_csv('combined_btc_data.csv')
reviews = pd.read_csv('trustpilot_coinbase_reviews-strip.csv', sep='|')

reviews = reviews[reviews['Date'].apply(is_date)]
reviews['Date'] = pd.to_datetime(reviews['Date'])

reviews['YearMonth'] = reviews['Date'].dt.to_period('M')

monthly_mean_rating = reviews.groupby('YearMonth')['Rating'].mean().reset_index()
monthly_mean_rating['Date'] = monthly_mean_rating['YearMonth'].dt.to_timestamp()

btc_all['Date'] = pd.to_datetime(btc_all['Date'])

btc_all['YearMonth'] = btc_all['Date'].dt.to_period('M')

btc_all = pd.merge(btc_all, monthly_mean_rating, on='YearMonth', how='left')
btc_all['Date'] =  btc_all['Date_x']
btc_all = btc_all.drop(columns=['Date_x', 'Date_y'])

btc_all['Rating'].fillna(method='ffill', inplace=True)

btc_all['Lag_Close_1'] = btc_all['Close'].shift(1)
btc_all['Lag_Close_2'] = btc_all['Close'].shift(2)
btc_all['Lag_Volume_1'] = btc_all['Volume'].shift(1)
btc_all['Lag_Volume_2'] = btc_all['Volume'].shift(2)

btc_all.dropna(inplace=True)

btc_all['Day'] = btc_all['Date'].dt.day
btc_all['Month'] = btc_all['Date'].dt.month
btc_all['Year'] = btc_all['Date'].dt.year

X = btc_all[['Lag_Close_1', 'Lag_Close_2', 'Lag_Volume_1', 'Lag_Volume_2', 'Day', 'Month', 'Year', 'Rating']]
y = btc_all['Close']

btc_all.sort_values('Date', inplace=True)

split_point = int(len(btc_all) * 0.80)
X_train = X.iloc[:split_point]
X_test = X.iloc[split_point:]
y_train = y.iloc[:split_point]
y_test = y.iloc[split_point:]

scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)

pipeline = Pipeline([
    ('scaler', StandardScaler()),
    ('poly', PolynomialFeatures()),
    ('model', LinearRegression())
])

param_grid = {
    'poly__degree': [1, 2, 3],
    'model': [LinearRegression()]
}

grid_search = GridSearchCV(pipeline, param_grid, cv=5, scoring='neg_mean_squared_error')
grid_search.fit(X_train, y_train)

best_model = grid_search.best_estimator_

eval_regression(X_train, X_test, y_train, y_test, best_model, "Best Model with Grid Search and Polynomial Features")


Best Model with Grid Search and Polynomial Features
Mean Squared (MSE): 1311689.86
Mean Absolute Error (MAE): 700.54
R^2: 0.99
Mean Absolute % (MAPE): 1.72%



In [ ]:
import pandas as pd
from sklearn.preprocessing import StandardScaler, PolynomialFeatures
from sklearn.linear_model import LinearRegression
from sklearn.model_selection import GridSearchCV
from sklearn.pipeline import Pipeline

btc_all = pd.read_csv('combined_btc_data.csv')
reviews = pd.read_csv('trustpilot_coinbase_reviews-strip.csv', sep='|')

reviews = reviews[reviews['Date'].apply(is_date)]
reviews['Date'] = pd.to_datetime(reviews['Date'])

reviews['YearMonth'] = reviews['Date'].dt.to_period('M')

monthly_mean_rating = reviews.groupby('YearMonth')['Rating'].mean().reset_index()
monthly_mean_rating['Date'] = monthly_mean_rating['YearMonth'].dt.to_timestamp()

btc_all['Date'] = pd.to_datetime(btc_all['Date'])

btc_all['YearMonth'] = btc_all['Date'].dt.to_period('M')

btc_all = pd.merge(btc_all, monthly_mean_rating, on='YearMonth', how='left')
btc_all['Date'] =  btc_all['Date_x']
btc_all = btc_all.drop(columns=['Date_x', 'Date_y'])

btc_all['Rating'].fillna(method='ffill', inplace=True)

btc_all['Lag_Close_1'] = btc_all['Close'].shift(1)
btc_all['Lag_Close_2'] = btc_all['Close'].shift(2)
btc_all['Lag_Volume_1'] = btc_all['Volume'].shift(1)
btc_all['Lag_Volume_2'] = btc_all['Volume'].shift(2)

btc_all.dropna(inplace=True)

btc_all['Day'] = btc_all['Date'].dt.day
btc_all['Month'] = btc_all['Date'].dt.month
btc_all['Year'] = btc_all['Date'].dt.year

X = btc_all[['Lag_Close_1', 'Lag_Close_2', 'Lag_Volume_1', 'Lag_Volume_2', 'Day', 'Month', 'Year', 'Rating']]
y = btc_all['Close']

btc_all.sort_values('Date', inplace=True)

split_point = int(len(btc_all) * 0.85)
X_train = X.iloc[:split_point]
X_test = X.iloc[split_point:]
y_train = y.iloc[:split_point]
y_test = y.iloc[split_point:]

scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)

pipeline = Pipeline([
    ('scaler', StandardScaler()),
    ('poly', PolynomialFeatures()),
    ('model', LinearRegression())
])

param_grid = {
    'poly__degree': [1, 2, 3],
    'model': [LinearRegression()]
}

grid_search = GridSearchCV(pipeline, param_grid, cv=5, scoring='neg_mean_squared_error')
grid_search.fit(X_train, y_train)

best_model = grid_search.best_estimator_

eval_regression(X_train, X_test, y_train, y_test, best_model, "Best Model with Grid Search and Polynomial Features")


Best Model with Grid Search and Polynomial Features
Mean Squared (MSE): 1601648.70
Mean Absolute Error (MAE): 779.05
R^2: 0.99
Mean Absolute % (MAPE): 1.67%



In [ ]:
import pandas as pd
from sklearn.preprocessing import StandardScaler, PolynomialFeatures
from sklearn.linear_model import LinearRegression

btc_all = pd.read_csv('combined_btc_data.csv')
reviews = pd.read_csv('trustpilot_coinbase_reviews-strip.csv', sep='|')

reviews = reviews[reviews['Date'].apply(is_date)]
reviews['Date'] = pd.to_datetime(reviews['Date'])

reviews['YearMonth'] = reviews['Date'].dt.to_period('M')

monthly_mean_rating = reviews.groupby('YearMonth')['Rating'].mean().reset_index()
monthly_mean_rating['Date'] = monthly_mean_rating['YearMonth'].dt.to_timestamp()

btc_all['Date'] = pd.to_datetime(btc_all['Date'])

btc_all['YearMonth'] = btc_all['Date'].dt.to_period('M')

btc_all = pd.merge(btc_all, monthly_mean_rating, on='YearMonth', how='left')
btc_all['Date'] =  btc_all['Date_x']
btc_all = btc_all.drop(columns=['Date_x', 'Date_y'])

btc_all['Rating'].fillna(method='ffill', inplace=True)

btc_all['Lag_Close_1'] = btc_all['Close'].shift(1)
btc_all['Lag_Close_2'] = btc_all['Close'].shift(2)
btc_all['Lag_Volume_1'] = btc_all['Volume'].shift(1)
btc_all['Lag_Volume_2'] = btc_all['Volume'].shift(2)

btc_all.dropna(inplace=True)

btc_all['Day'] = btc_all['Date'].dt.day
btc_all['Month'] = btc_all['Date'].dt.month
btc_all['Year'] = btc_all['Date'].dt.year

X = btc_all[['Lag_Close_1', 'Lag_Close_2', 'Lag_Volume_1', 'Lag_Volume_2', 'Day', 'Month', 'Year', 'Rating']]
y = btc_all['Close']

btc_all.sort_values('Date', inplace=True)

split_point = int(len(btc_all) * 0.85)
X_train = X.iloc[:split_point]
X_test = X.iloc[split_point:]
y_train = y.iloc[:split_point]
y_test = y.iloc[split_point:]

scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)

# Linear model
linear_model = LinearRegression()
linear_model.fit(X_train, y_train)
eval_regression(X_train, X_test, y_train, y_test, linear_model, "Linear Regression Model:")

# Polynomial model
poly = PolynomialFeatures(degree=2)
X_train_poly = poly.fit_transform(X_train)
X_test_poly = poly.transform(X_test)

poly_model = LinearRegression()
poly_model.fit(X_train_poly, y_train)
eval_regression(X_train_poly, X_test_poly, y_train, y_test, poly_model, "Polynomial Regression Model:")



Linear Regression Model:
Mean Squared (MSE): 1601648.70
Mean Absolute Error (MAE): 779.05
R^2: 0.99
Mean Absolute % (MAPE): 1.67%

Polynomial Regression Model:
Mean Squared (MSE): 1980812.82
Mean Absolute Error (MAE): 893.67
R^2: 0.99
Mean Absolute % (MAPE): 1.92%



In [ ]:
grid_search.best_params_ 

{'model': LinearRegression(), 'poly__degree': 1}

Degree 1 = NoPoly

### Pridedame daugiau parametrų:

In [ ]:
from sklearn.linear_model import LinearRegression, Ridge, Lasso
from sklearn.model_selection import GridSearchCV
from sklearn.pipeline import Pipeline

scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)

pipeline = Pipeline([
    ('scaler', StandardScaler()),
    ('poly', PolynomialFeatures()),
    ('model', LinearRegression())
])

param_grid = [
    {
        'poly__degree': [i for i in range(1, 11)],
        'model': [LinearRegression(random_state=seed) for seed in range(5)] 
    },
    {
        'poly__degree': [i for i in range(1, 4)],
        'model': [Ridge()],
        'model__alpha': [1, 10, 100]
    },
    {
        'poly__degree': [i for i in range(1, 4)],
        'model': [Lasso()],
        'model__alpha': [1, 10, 100]
    }
]


grid_search = GridSearchCV(pipeline, param_grid, cv=5, scoring='neg_mean_squared_error', verbose=2)
grid_search.fit(X_train, y_train)

best_model = grid_search.best_estimator_

eval_regression(X_train, X_test, y_train, y_test, best_model, "Best Model with Grid Search and Poly, ext parameters + seed search:")

Fitting 5 folds for each of 28 candidates, totalling 140 fits
[CV] END ...........model=LinearRegression(), poly__degree=1; total time=   0.0s
[CV] END ...........model=LinearRegression(), poly__degree=1; total time=   0.0s
[CV] END ...........model=LinearRegression(), poly__degree=1; total time=   0.0s
[CV] END ...........model=LinearRegression(), poly__degree=1; total time=   0.0s
[CV] END ...........model=LinearRegression(), poly__degree=1; total time=   0.0s
[CV] END ...........model=LinearRegression(), poly__degree=2; total time=   0.0s
[CV] END ...........model=LinearRegression(), poly__degree=2; total time=   0.0s
[CV] END ...........model=LinearRegression(), poly__degree=2; total time=   0.0s
[CV] END ...........model=LinearRegression(), poly__degree=2; total time=   0.0s
[CV] END ...........model=LinearRegression(), poly__degree=2; total time=   0.0s
[CV] END ...........model=LinearRegression(), poly__degree=3; total time=   0.0s
[CV] END ...........model=LinearRegression(), p

c:\Documents\PythonMokymai repo\PythonMokymai0\mokymai\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:628: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 8.100e+08, tolerance: 5.000e+07
  model = cd_fast.enet_coordinate_descent(


[CV] END ......model=Lasso(), model__alpha=1, poly__degree=3; total time=   0.4s


c:\Documents\PythonMokymai repo\PythonMokymai0\mokymai\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:628: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 8.623e+08, tolerance: 5.001e+07
  model = cd_fast.enet_coordinate_descent(


[CV] END ......model=Lasso(), model__alpha=1, poly__degree=3; total time=   0.5s


...

[CV] END ......model=Lasso(), model__alpha=1, poly__degree=3; total time=   0.4s


c:\Documents\PythonMokymai repo\PythonMokymai0\mokymai\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:628: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 7.514e+08, tolerance: 5.331e+07
  model = cd_fast.enet_coordinate_descent(


[CV] END ......model=Lasso(), model__alpha=1, poly__degree=3; total time=   0.5s
[CV] END .....model=Lasso(), model__alpha=10, poly__degree=1; total time=   0.0s
[CV] END .....model=Lasso(), model__alpha=10, poly__degree=1; total time=   0.0s
[CV] END .....model=Lasso(), model__alpha=10, poly__degree=1; total time=   0.0s
[CV] END .....model=Lasso(), model__alpha=10, poly__degree=1; total time=   0.0s
[CV] END .....model=Lasso(), model__alpha=10, poly__degree=1; total time=   0.0s
[CV] END .....model=Lasso(), model__alpha=10, poly__degree=2; total time=   0.0s
[CV] END .....model=Lasso(), model__alpha=10, poly__degree=2; total time=   0.0s
[CV] END .....model=Lasso(), model__alpha=10, poly__degree=2; total time=   0.0s
[CV] END .....model=Lasso(), model__alpha=10, poly__degree=2; total time=   0.0s
[CV] END .....model=Lasso(), model__alpha=10, poly__degree=2; total time=   0.0s
[CV] END .....model=Lasso(), model__alpha=10, poly__degree=3; total time=   0.3s
[CV] END .....model=Lasso(),

c:\Documents\PythonMokymai repo\PythonMokymai0\mokymai\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:628: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 2.084e+08, tolerance: 5.331e+07
  model = cd_fast.enet_coordinate_descent(


[CV] END .....model=Lasso(), model__alpha=10, poly__degree=3; total time=   0.3s
[CV] END ....model=Lasso(), model__alpha=100, poly__degree=1; total time=   0.0s
[CV] END ....model=Lasso(), model__alpha=100, poly__degree=1; total time=   0.0s
[CV] END ....model=Lasso(), model__alpha=100, poly__degree=1; total time=   0.0s
[CV] END ....model=Lasso(), model__alpha=100, poly__degree=1; total time=   0.0s
[CV] END ....model=Lasso(), model__alpha=100, poly__degree=1; total time=   0.0s
[CV] END ....model=Lasso(), model__alpha=100, poly__degree=2; total time=   0.0s
[CV] END ....model=Lasso(), model__alpha=100, poly__degree=2; total time=   0.0s
[CV] END ....model=Lasso(), model__alpha=100, poly__degree=2; total time=   0.0s
[CV] END ....model=Lasso(), model__alpha=100, poly__degree=2; total time=   0.0s
[CV] END ....model=Lasso(), model__alpha=100, poly__degree=2; total time=   0.0s
[CV] END ....model=Lasso(), model__alpha=100, poly__degree=3; total time=   0.0s
[CV] END ....model=Lasso(), 

In [ ]:
import shutil

def print_all_models(results):
    terminal_width = shutil.get_terminal_size().columns
    terminal_width *= 2 if terminal_width == 80 else terminal_width
    for i in range(len(results['params'])):
        print(f"Model {i}: || Rank: {results['rank_test_score'][i]} || Parameters: {results['params'][i]} || Mean Test Score(best=0): {results['mean_test_score'][i]}")
        print('='*terminal_width)

print_all_models(grid_search.cv_results_)


Model 0: || Rank: 3 || Parameters: {'model': LinearRegression(), 'poly__degree': 1} || Mean Test Score(best=0): -922988.670489825
Model 1: || Rank: 13 || Parameters: {'model': LinearRegression(), 'poly__degree': 2} || Mean Test Score(best=0): -3040558.790308443
Model 2: || Rank: 20 || Parameters: {'model': LinearRegression(), 'poly__degree': 3} || Mean Test Score(best=0): -257448251.76484418
Model 3: || Rank: 22 || Parameters: {'model': LinearRegression(), 'poly__degree': 4} || Mean Test Score(best=0): -46139966668.20374
Model 4: || Rank: 23 || Parameters: {'model': LinearRegression(), 'poly__degree': 5} || Mean Test Score(best=0): -8.761141605548803e+16
Model 5: || Rank: 24 || Parameters: {'model': LinearRegression(), 'poly__degree': 6} || Mean Test Score(best=0): -4.7987076821791664e+20
Model 6: || Rank: 25 || Parameters: {'model': LinearRegression(), 'poly__degree': 7} || Mean Test Score(best=0): -3.97895441926736e+21
Model 7: || Rank: 26 || Parameters: {'model': LinearRegression(),

In [ ]:
grid_search.best_estimator_

Pipeline(steps=[('scaler', StandardScaler()),
                ('poly', PolynomialFeatures(degree=1)),
                ('model', Lasso(alpha=10))])

In [ ]:
param_grid = [
    {
        'poly__degree': [1],
        'model': [LinearRegression()]
    },
    {
        'poly__degree': [1],
        'model': [Ridge(random_state=seed) for seed in range(100)],
        'model__alpha': [1, 10, 25, 50, 75]
    },
    {
        'poly__degree': [1],
        'model': [Lasso(random_state=seed) for seed in range(100)],
        'model__alpha': [1, 10, 25, 50, 75]
    }
]

grid_search = GridSearchCV(pipeline, param_grid, cv=5, scoring='neg_mean_squared_error', verbose=2)
grid_search.fit(X_train, y_train)

best_model = grid_search.best_estimator_

eval_regression(X_train, X_test, y_train, y_test, best_model, "Best Model with Grid Search - seed search:")

Fitting 5 folds for each of 1001 candidates, totalling 5005 fits
[CV] END ...........model=LinearRegression(), poly__degree=1; total time=   0.0s
[CV] END ...........model=LinearRegression(), poly__degree=1; total time=   0.0s
[CV] END ...........model=LinearRegression(), poly__degree=1; total time=   0.0s
[CV] END ...........model=LinearRegression(), poly__degree=1; total time=   0.0s
[CV] END ...........model=LinearRegression(), poly__degree=1; total time=   0.0s
[CV] END model=Ridge(random_state=0), model__alpha=1, poly__degree=1; total time=   0.0s
[CV] END model=Ridge(random_state=0), model__alpha=1, poly__degree=1; total time=   0.0s
[CV] END model=Ridge(random_state=0), model__alpha=1, poly__degree=1; total time=   0.0s
[CV] END model=Ridge(random_state=0), model__alpha=1, poly__degree=1; total time=   0.0s
[CV] END model=Ridge(random_state=0), model__alpha=1, poly__degree=1; total time=   0.0s
[CV] END model=Ridge(random_state=0), model__alpha=10, poly__degree=1; total time=   

In [ ]:
grid_search.best_estimator_

Pipeline(steps=[('scaler', StandardScaler()),
                ('poly', PolynomialFeatures(degree=1)),
                ('model', Lasso(alpha=10, random_state=0))])

In [ ]:
eval_regression(X_train, X_test, y_train, y_test, linear_model, "Linear Regression Model:")
eval_regression(X_train, X_test, y_train, y_test, best_model, "Best Model with Grid Search - seed search:")

Linear Regression Model:
Mean Squared (MSE): 1601648.70
Mean Absolute Error (MAE): 779.05
R^2: 0.99
Mean Absolute % (MAPE): 1.67%

Best Model with Grid Search - seed search:
Mean Squared (MSE): 1616735.66
Mean Absolute Error (MAE): 784.50
R^2: 0.99
Mean Absolute % (MAPE): 1.68%



In [ ]:
from sklearn.model_selection import cross_val_score
import numpy as np

def eval_regression_cv(X, y, model, model_name):
    mse_scores = cross_val_score(model, X, y, scoring='neg_mean_squared_error', cv=5)
    mae_scores = cross_val_score(model, X, y, scoring='neg_mean_absolute_error', cv=5)
    r2_scores = cross_val_score(model, X, y, scoring='r2', cv=5) # cv --> no of equal parts, train on cv-1

    print(f"{model_name}")
    print(f"Mean Squared Error (MSE): {-np.mean(mse_scores):.2f}")
    print(f"Mean Absolute Error (MAE): {-np.mean(mae_scores):.2f}")
    print(f"R^2: {np.mean(r2_scores):.2f}")
    print("="*50)

X = np.concatenate([X_train, X_test])
y = np.concatenate([y_train, y_test])

linear_model = LinearRegression()
eval_regression_cv(X, y, linear_model, "cross_val Linear Regression:")

best_model = grid_search.best_estimator_ # Lasso (linear + regularization)
eval_regression_cv(X, y, best_model, "cross_val Grid Search - seed search, best (Lasso):")


cross_val Linear Regression:
Mean Squared Error (MSE): 1018571.67
Mean Absolute Error (MAE): 560.09
R^2: 0.99
cross_val Grid Search - seed search, best (Lasso):
Mean Squared Error (MSE): 1008962.65
Mean Absolute Error (MAE): 557.90
R^2: 0.99


In [ ]:
grid_search.best_params_

{'model': Lasso(random_state=0), 'model__alpha': 10, 'poly__degree': 1}

### RandomForest bandymai:

In [ ]:
import pandas as pd
from sklearn.preprocessing import StandardScaler
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_squared_error
from sklearn.model_selection import GridSearchCV

btc_all = pd.read_csv('combined_btc_data.csv')
reviews = pd.read_csv('trustpilot_coinbase_reviews-strip.csv', sep='|')

reviews['Date'] = pd.to_datetime(reviews['Date'], errors='coerce')
reviews = reviews.dropna(subset=['Date'])
reviews['YearMonth'] = reviews['Date'].dt.to_period('M')

monthly_mean_rating = reviews.groupby('YearMonth')['Rating'].mean().reset_index()
monthly_mean_rating['Date'] = monthly_mean_rating['YearMonth'].dt.to_timestamp()

btc_all['Date'] = pd.to_datetime(btc_all['Date'])
btc_all['YearMonth'] = btc_all['Date'].dt.to_period('M')

btc_all = pd.merge(btc_all, monthly_mean_rating, on='YearMonth', how='left')
btc_all['Date'] =  btc_all['Date_x']
btc_all = btc_all.drop(columns=['Date_x', 'Date_y'])

btc_all['Rating'].fillna(method='ffill', inplace=True)

btc_all['Lag_Close_1'] = btc_all['Close'].shift(1)
btc_all['Lag_Close_2'] = btc_all['Close'].shift(2)
btc_all['Lag_Volume_1'] = btc_all['Volume'].shift(1)
btc_all['Lag_Volume_2'] = btc_all['Volume'].shift(2)

btc_all.dropna(inplace=True)

btc_all['Day'] = btc_all['Date'].dt.day
btc_all['Month'] = btc_all['Date'].dt.month
btc_all['Year'] = btc_all['Date'].dt.year

X = btc_all[['Lag_Close_1', 'Lag_Close_2', 'Lag_Volume_1', 'Lag_Volume_2', 'Day', 'Month', 'Year', 'Rating']]
y = btc_all['Close']

btc_all.sort_values('Date', inplace=True)

split_point = int(len(btc_all) * 0.85)
X_train = X.iloc[:split_point]
X_test = X.iloc[split_point:]
y_train = y.iloc[:split_point]
y_test = y.iloc[split_point:]

scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)

rf = RandomForestRegressor(random_state=0)

# Define parameter grid for GridSearchCV
param_grid = {
    'n_estimators': [100, 200, 300],
    'max_depth': [None, 10, 20, 30],
    'min_samples_split': [2, 5, 10],
    'min_samples_leaf': [1, 2, 4]
}


grid_search = GridSearchCV(estimator=rf, param_grid=param_grid, cv=5, n_jobs=-1, scoring='neg_mean_squared_error', verbose=2)
grid_search.fit(X_train, y_train)

best_model = grid_search.best_estimator_

y_pred = best_model.predict(X_test)

mse = mean_squared_error(y_test, y_pred)

print(f'Mean Squared Error: {mse}')
print(f'Best Params: {grid_search.best_params_}')


Fitting 5 folds for each of 108 candidates, totalling 540 fits
Mean Squared Error: 4996052.775517814
Best Params: {'max_depth': None, 'min_samples_leaf': 2, 'min_samples_split': 2, 'n_estimators': 100}


In [ ]:
best_model = grid_search.best_estimator_
eval_regression_cv(X, y, best_model, "Best random forest:")

Best random forest:
Mean Squared Error (MSE): 1944100.14
Mean Absolute Error (MAE): 829.50
R^2: 0.98


### RandomForest SEED paieška

In [ ]:
rf_best_param = grid_search.best_params_

results = []
for seed in range(100):
    rf = RandomForestRegressor(random_state=seed, **rf_best_param)
    rf.fit(X_train, y_train)
    
    y_pred = rf.predict(X_test)
    mse = mean_squared_error(y_test, y_pred)
    mae = mean_absolute_error(y_test, y_pred)
    r2 = r2_score(y_test, y_pred)
    
    results.append({
        'seed': seed,
        'mse': mse,
        'mae': mae,
        'r2': r2
    })
for result in results:
    print(f"Random Seed: {result['seed']}")
    print(f"Mean Squared Error (MSE): {result['mse']}")
    print(f"Mean Absolute Error (MAE): {result['mae']}")
    print(f"R^2: {result['r2']}")
    print("="*50)

Random Seed: 0
Mean Squared Error (MSE): 4996052.775517814
Mean Absolute Error (MAE): 1501.4247457178783
R^2: 0.9794782977603431
Random Seed: 1
Mean Squared Error (MSE): 5125072.549682068
Mean Absolute Error (MAE): 1533.555984498857
R^2: 0.9789483383088735
Random Seed: 2
Mean Squared Error (MSE): 5054499.405879303
Mean Absolute Error (MAE): 1557.7345543607014
R^2: 0.9792382233657996
Random Seed: 3
Mean Squared Error (MSE): 4935535.728085683
Mean Absolute Error (MAE): 1521.3443166752927
R^2: 0.979726876565177
Random Seed: 4
Mean Squared Error (MSE): 4973150.644626401
Mean Absolute Error (MAE): 1528.3114010362046
R^2: 0.9795723701674862
Random Seed: 5
Mean Squared Error (MSE): 5052138.78915618
Mean Absolute Error (MAE): 1519.7293451808173
R^2: 0.9792479197952951
Random Seed: 6
Mean Squared Error (MSE): 5020800.998398905
Mean Absolute Error (MAE): 1509.4070503462258
R^2: 0.9793766423768341
Random Seed: 7
Mean Squared Error (MSE): 4892024.960268405
Mean Absolute Error (MAE): 1507.009784314

In [ ]:
best_rf_seed = min(results, key=lambda x: x['mse'])

print("Best Model based on MSE:")
print(f"Random Seed: {best_rf_seed['seed']}")
print(f"Mean Squared Error (MSE): {best_rf_seed['mse']}")
print(f"Mean Absolute Error (MAE): {best_rf_seed['mae']}")
print(f"R^2: {best_rf_seed['r2']}")
print("="*50)

Best Model based on MSE:
Random Seed: 73
Mean Squared Error (MSE): 4768115.97634129
Mean Absolute Error (MAE): 1483.8083762392123
R^2: 0.9804145671178413


In [ ]:
import pandas as pd
from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import Lasso
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import mean_squared_error

btc_all = pd.read_csv('combined_btc2_data.csv')
reviews = pd.read_csv('trustpilot_coinbase_reviews-strip.csv', sep='|')

reviews['Date'] = pd.to_datetime(reviews['Date'], errors='coerce')
reviews = reviews.dropna(subset=['Date'])
reviews['YearMonth'] = reviews['Date'].dt.to_period('M')
monthly_mean_rating = reviews.groupby('YearMonth')['Rating'].mean().reset_index()
monthly_mean_rating['Date'] = monthly_mean_rating['YearMonth'].dt.to_timestamp()

btc_all['Date'] = pd.to_datetime(btc_all['Date'])
btc_all['YearMonth'] = btc_all['Date'].dt.to_period('M')

btc_all = pd.merge(btc_all, monthly_mean_rating, on='YearMonth', how='left')
btc_all['Date'] = btc_all['Date_x']
btc_all = btc_all.drop(columns=['Date_x', 'Date_y'])
btc_all['Rating'].fillna(method='ffill', inplace=True)

btc_all['Lag_Close_1'] = btc_all['Close'].shift(1)
btc_all['Lag_Close_2'] = btc_all['Close'].shift(2)
btc_all['Lag_Volume_1'] = btc_all['Volume'].shift(1)
btc_all['Lag_Volume_2'] = btc_all['Volume'].shift(2)
btc_all['Lag_Open_1'] = btc_all['Open'].shift(1)
btc_all['Lag_Open_2'] = btc_all['Open'].shift(2)
btc_all['Lag_High_1'] = btc_all['High'].shift(1)
btc_all['Lag_High_2'] = btc_all['High'].shift(2)
btc_all['Lag_Low_1'] = btc_all['Low'].shift(1)
btc_all['Lag_Low_2'] = btc_all['Low'].shift(2)

btc_all.dropna(inplace=True)

btc_all['Day'] = btc_all['Date'].dt.day
btc_all['Month'] = btc_all['Date'].dt.month
btc_all['Year'] = btc_all['Date'].dt.year

X = btc_all[['Lag_Close_1', 'Lag_Close_2', 'Lag_Volume_1', 'Lag_Volume_2', 'Lag_Open_1', 'Lag_Open_2', 'Lag_High_1', 'Lag_High_2', 'Lag_Low_1', 'Lag_Low_2', 'Open', 'High', 'Low', 'Day', 'Month', 'Year', 'Rating']]
y = btc_all['Close']

assert len(X) == len(y), "Feature and target arrays do not have the same length"

split_point = int(len(btc_all) * 0.85)
X_train = X.iloc[:split_point].copy()
X_test = X.iloc[split_point:].copy()
y_train = y.iloc[:split_point].copy()
y_test = y.iloc[split_point:].copy()

assert len(X_train) == len(y_train), "Training feature and target arrays do not have the same length"
assert len(X_test) == len(y_test), "Test feature and target arrays do not have the same length"

scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)

lasso = Lasso(random_state=0)

param_grid = {
    'alpha': [75, 100, 130], # 75 is lowest without convergence warning
    'max_iter': [25000, 100000, 300000, 500000],
    'tol': [0.0001, 0.00001, 0.001, 0.01]
}

grid_search = GridSearchCV(estimator=lasso, param_grid=param_grid, cv=5, n_jobs=-1, scoring='neg_mean_squared_error', verbose=2)
grid_search.fit(X_train, y_train)

best_model = grid_search.best_estimator_
y_pred = best_model.predict(X_test)
mse = mean_squared_error(y_test, y_pred)

print(f'Mean Squared Error: {mse}')
print(f'Best Params: {grid_search.best_params_}')
lasso_params = grid_search.best_params_


Fitting 5 folds for each of 48 candidates, totalling 240 fits
Mean Squared Error: 420941.00918314257
Best Params: {'alpha': 75, 'max_iter': 25000, 'tol': 0.001}


In [ ]:
split_point = int(len(btc_all) * 0.85)
X_train = X.iloc[:split_point].copy()
X_test = X.iloc[split_point:].copy()
y_train = y.iloc[:split_point].copy()
y_test = y.iloc[split_point:].copy()

lasso = Lasso(**lasso_params, random_state=0)
lasso.fit(X_train, y_train)
y_pred = lasso.predict(X_test)
eval_regression(X_train, X_test, y_train, y_test, best_model, "Lasso 0:")

Lasso 0:
Mean Squared (MSE): 299080.84
Mean Absolute Error (MAE): 370.32
R^2: 1.00
Mean Absolute % (MAPE): 0.82%



Lasso su Convergence perspėjimu (overfitting): <br>
- Mean Squared (MSE): 162928.95 
- Mean Absolute Error (MAE): 282.09 
- Mean Absolute % (MAPE): 0.64% 

In [ ]:
lasso_params

{'alpha': 75, 'max_iter': 25000, 'tol': 0.001}

In [ ]:
split_point = int(len(btc_all) * 0.85)
X_train = X.iloc[:split_point].copy()
X_test = X.iloc[split_point:].copy()
y_train = y.iloc[:split_point].copy()
y_test = y.iloc[split_point:].copy()

lasso = Lasso(**lasso_params, random_state=0) 
lasso.fit(X_train, y_train)
y_pred = lasso.predict(X_test)
eval_regression(X_train, X_test, y_train, y_test, best_model, "Lasso 0:")

Lasso 0:
Mean Squared (MSE): 299080.84
Mean Absolute Error (MAE): 370.32
R^2: 1.00
Mean Absolute % (MAPE): 0.82%



### ^ net ir be convergence klaidos (eliminavus "overfitting"), Lasso (linear regression + regularization) matome kad susitvarko geriausiai ir rodo geriausius rezultatus, lenkiant RandomForest. Lasso atveju random_state su mūsų duomenimis įtakos nedaro, tad seed paieškos žingsį praleidžiu. 